In [2]:
import itertools
import numpy as np
import os
from tqdm import tqdm
import vsketch
import shapely.geometry as sg
from shapely.geometry import box, MultiLineString, Point, MultiPoint, Polygon, MultiPolygon, LineString
import shapely.affinity as sa
import shapely.ops as so
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns

from genpen import genpen as gp, utils as utils
from scipy import stats as ss
import geopandas
import functools

%load_ext autoreload
%autoreload 2

from genpen.utils import Paper
import bezier
from dataclasses import asdict, dataclass, field

In [2]:
# make page
paper_size = '11x17 inches'
border:float=35
paper = Paper(paper_size)

drawbox = paper.get_drawbox(border)

In [54]:
xstep = 25
ystep = 25
(xbins, ybins), (xs, ys) = gp.overlay_grid(drawbox, xstep=xstep, ystep=ystep, flatmesh=True)

In [71]:
pts = []
for i, y in enumerate(ybins):
    for x in xbins:
        if (i % 2) == 0:
            x += xstep/4
        else:
            x += -xstep/4
        pts.append(Point(x,y))

In [124]:
pts = MultiPoint(pts)
tris = so.triangulate(pts)
tris = [t for t in tris if t.intersects(drawbox.buffer(-21))]

In [126]:
yrange = [drawbox.bounds[1]+40, drawbox.bounds[2]]

In [127]:
jts = []
for t in tris:
    y = t.centroid.y
    angle_max = np.interp(y, yrange, [0, 10])
    angle = np.random.uniform(-angle_max, angle_max)
    jt = sa.rotate(t, angle)
    
    scale_max = np.interp(y, yrange, [0, 1.2])
    scale = np.random.uniform(1, 1+scale_max)
    jt = sa.scale(jt, xfact=scale, yfact=scale)
    
    jt = jt.buffer(-1, cap_style=2, join_style=1)
    jts.append(jt)

In [128]:
boundaries = gp.merge_Polygons(jts).boundary

In [129]:
bbs = so.unary_union([b.buffer(0.3, cap_style=1, join_style=1) for b in boundaries])

In [135]:
bbbs = gp.merge_LineStrings([b.boundary for b in bbs if b.area > 1])
bbbs = gp.merge_Polygons([Polygon(b) for b in bbbs]).buffer(-0.1)
bbbs = so.unary_union([b.buffer(0.1, cap_style=1, join_style=1) for b in bbs.boundary])
bbbs = gp.merge_LineStrings([b.boundary for b in bbbs if b.area < 1e2])
bbbs = gp.merge_Polygons([Polygon(b).buffer(-0.1) for b in bbbs])

In [142]:
bbbs = so.unary_union(bbbs)

In [145]:
n_layers = 1
all_layers = [list() for i in range(n_layers)]
    
layer_choices = np.random.choice(n_layers, size=len(bbbs))
for i, lc in enumerate(layer_choices):
    p = bbbs[i]
    y = p.centroid.y
    angle_max = np.interp(y, yrange, [3, 50])
    angle = np.random.uniform(-angle_max, angle_max)
    
    spacing_range = np.interp(y, yrange, [0, 0.2])
    spacing = np.random.uniform(0.7-spacing_range, 0.7 + spacing_range)
    hatches = gp.hatchbox(p, spacing=spacing, angle=angle)
    all_layers[lc].append(hatches)
    
all_hatch_layers = []
for layer in all_layers:
    hatch_layer = [ls for ls in layer if ls.length > 1e-2]
    all_hatch_layers.append(gp.merge_LineStrings(hatch_layer))

In [146]:
sk = vsketch.Vsketch()
sk.size(paper.page_format_mm)
sk.scale('1mm')
sk.penWidth('0.5mm')
for i, layer in enumerate(all_hatch_layers):
    sk.stroke(i+1)
    sk.geometry(layer)

for tolerance in [1.2, 1.5]:
    sk.vpype(f'linesort linemerge --tolerance {tolerance}mm')
sk.vpype('linesimplify -t 0.2mm')
sk.vpype('linesort')
sk.display(color_mode='layer')

<?xml version="1.0" encoding="utf-8" ?>
 
 
 
 
 image/svg+xml 
 
 2021-01-19T21:15:18.894706 
 
 
 
 
 
 <polyline points="275.8279,127.0716 250.3907,127.1805 250.4149,129.8261 333.7654,129.4694 332.4397,132.1208 251.7349,132.4661 253.0549,135.1062 331.114,134.7721 329.7884,137.4235 254.375,137.7462 255.695,140.3862 328.4627,140.0749 327.137,142.7262 257.015,143.0263 258.335,145.6663 325.8113,145.3776 324.4856,148.029 259.6551,148.3064 260.9751,150.9464 323.1599,150.6803 321.8343,153.3317 262.2951,153.5865 263.6151,156.2265 320.5086,155.9831 319.1829,158.6344 264.9351,158.8666 266.2552,161.5066 317.8572,161.2858 316.5315,163.9372 267.5752,164.1466 268.8952,166.7867 315.2058,166.5885 313.8802,169.2399 270.2152,169.4267 271.5353,172.0668 312.5545,171.8913 311.2288,174.5426 272.8553,174.7068 274.1753,177.3469 309.9031,177.194 308.5774,179.8454 275.4953,179.9869 276.8153,182.627 307.2517,182.4967 305.9261,185.1481 278.1354,185.267 279.4554,187.9071 304.6004,187.7995 303.2747,190.4508 280.7754,190.5471 282.0954,193.1871 301.949,193.1022 300.6233,195.7536 283.4155,195.8272 284.7355,198.4672 299.2976,198.4049 297.972,201.0563 286.0555,201.1073 287.3755,203.7473 296.6463,203.7077 295.3206,206.359 288.6955,206.3874 290.0156,209.0274 293.9949,209.0104"/>
 <polyline points="286.9973,214.9164 247.482,216.2685 247.697,221.5598 287.0176,222.7314 285.8287,225.3428 202.5077,222.8602 203.7862,225.5451 284.5247,227.9508 283.2207,230.5588 205.1297,228.232 206.4731,230.9189 281.9167,233.1668 280.6127,235.7748 207.8165,233.6057 209.16,236.2926 279.3087,238.3828 278.0047,240.9908 210.5034,238.9795 211.8469,241.6664 276.7007,243.5988 275.3967,246.2068 213.1903,244.3532 214.5337,247.0401 274.0927,248.8147 272.7887,251.4227 215.8772,249.727 217.2206,252.4139 271.4848,254.0307 270.1808,256.6387 218.564,255.1007 219.9075,257.7876 268.8768,259.2467 267.5728,261.8547 221.2509,260.4745 222.5943,263.1613 266.2688,264.4627 264.9648,267.0707 223.9378,265.8482 225.2812,268.5351 263.6608,269.6787 262.3568,272.2866 226.6247,271.222 227.9681,273.9088 261.0528,274.8946 259.7488,277.5026 229.3115,276.5957 230.655,279.2826 258.4448,280.1106 257.1408,282.7186 231.9984,281.9695 233.3418,284.6563 255.8368,285.3266 254.5328,287.9346 234.6853,287.3432 236.0287,290.0301 253.2288,290.5426 251.9248,293.1506 237.3721,292.7169 238.7156,295.4038 250.6208,295.7586 249.3168,298.3665 240.059,298.0907 241.4025,300.7776 248.0128,300.9745 246.7089,303.5825 242.7459,303.4644"/>
 
 
 
 <polyline points="158.3081,320.5513 231.2709,327.9161 230.0678,330.4229 159.7516,323.3253 161.1951,326.0992 228.8647,332.9296 227.6616,335.4364 162.6386,328.8731 164.0821,331.647 226.4585,337.9432 225.2554,340.4499 165.5256,334.4209 166.9691,337.1948 224.0523,342.9567 222.8492,345.4635 168.4126,339.9687 169.8561,342.7426 221.6461,347.9702 220.443,350.477 171.2996,345.5165 172.7431,348.2904 219.2399,352.9837 218.0368,355.4905 174.1866,351.0643 175.6301,353.8382 216.8337,357.9973 215.6306,360.504 177.0736,356.6121 178.5171,359.386 214.4275,363.0108 213.2244,365.5176 179.9606,362.16 181.4041,364.9339 212.0213,368.0243 210.8182,370.5311 182.8476,367.7078 184.2911,370.4817 209.6151,373.0378 208.412,375.5446 185.7346,373.2556 187.1781,376.0295 207.2089,378.0514 206.0058,380.5581 188.6216,378.8034 190.0651,381.5773 204.8027,383.0649 203.5996,385.5717 191.5086,384.3512 192.9521,387.1251 202.3965,388.0784 201.1934,390.5852 194.3956,389.899 195.8391,392.6729 199.9903,393.092 198.7872,395.5987 197.2826,395.4468"/>
 
 <polyline points="250.2397,399.0376 284.7514,397.9942 283.5041,395.3731 202.922,397.8095 204.3393,395.1078 282.2568,392.752 281.0095,390.131 205.7566,392.4062 207.1738,389.7046 279.7622,387.5099 278.5149,384.8888 208.5911,387.0029 210.0084,384.3013 277.2676,382.2677 276.0203,379.6467 211.4257,381.5996 212.843,378.898 274.773,377.0256 273.5257,374.4045 214.2603,376.1964 215.6776,373.4947 272.2784,371.7834 271.0311,369.1624 217.0949,370.7931 218.5121,368.0914 269.7838,366.5413 268.5365,363.9202 219.929

In [147]:
sk.save('/mnt/c/code/side/plotter_images/oned_outputs/231_randomness_y.svg')

In [3]:
# make page
paper_size = '11x17 inches'
border:float=35
paper = Paper(paper_size)

drawbox = paper.get_drawbox(border)

In [56]:
xstep = 3
ystep = 3
(xbins, ybins), (xs, ys) = gp.overlay_grid(drawbox, xstep=xstep, ystep=ystep, flatmesh=True)

In [83]:
pts = []
for i, y in enumerate(ybins):
    for x in xbins:
        if (i % 2) == 0:
            x += xstep/4
        else:
            x += -xstep/4
        std = np.interp(i, [20, len(ybins)], [0, 3]) ** 2
        coord = np.array([x,y]) + np.random.randn(2) * std
        pts.append(Point(*coord))

In [84]:
pts = MultiPoint(pts)
tris = so.triangulate(pts)
tris = [t for t in tris if t.intersects(drawbox.buffer(-23))]

In [85]:
gp.merge_Polygons(tris)

In [98]:
jts = []
yrange = [drawbox.bounds[1]+180, drawbox.bounds[2]]
for t in tris:
    y = t.centroid.y
#     angle_max = np.interp(y, yrange, [0, 10])
#     angle = np.random.uniform(-angle_max, angle_max)
    jt = sa.rotate(t, 0)
    
    scale_max = np.interp(y, yrange, [0, 0.3])
    scale = np.random.uniform(1, 1+scale_max)
    jt = sa.scale(jt, xfact=scale, yfact=scale)
    
    jt = jt.buffer(-0.05, cap_style=2, join_style=2)
    jts.append(jt)

In [99]:
morphed = gp.merge_Polygons(jts)

In [101]:
n_layers = 1
all_layers = [list() for i in range(n_layers)]
yrange = [drawbox.bounds[1]+60, drawbox.bounds[2]]    
layer_choices = np.random.choice(n_layers, size=len(morphed))
for i, lc in enumerate(layer_choices):
    p = morphed[i]
    y = p.centroid.y
    angle_max = np.interp(y, yrange, [0, 13]) ** 2
    angle = np.random.uniform(-angle_max, angle_max)
    
    spacing_range = np.interp(y, yrange, [0, 0.4])
    spacing = np.random.uniform(0.65-spacing_range, 0.6 + spacing_range)
    hatches = gp.hatchbox(p, spacing=spacing, angle=angle)
    all_layers[lc].append(hatches)
    
all_hatch_layers = []
for layer in all_layers:
    hatch_layer = [ls for ls in layer if ls.length > 1e-2]
    all_hatch_layers.append(gp.merge_LineStrings(hatch_layer))

In [102]:
sk = vsketch.Vsketch()
sk.size(paper.page_format_mm)
sk.scale('1mm')
sk.penWidth('0.5mm')
for i, layer in enumerate(all_hatch_layers):
    sk.stroke(i+1)
    sk.geometry(layer)

for tolerance in [0.2, 0.5, 1, 2, 2]:
    sk.vpype(f'linemerge --tolerance {tolerance}mm linesort ')
sk.vpype('linesimplify -t 0.1mm')
sk.vpype('linesort')
sk.display(color_mode='layer')

<?xml version="1.0" encoding="utf-8" ?>
 
 
 
 
 image/svg+xml 
 
 2021-01-20T18:50:11.851887 
 
 
 
 
 
 <polyline points="232.4686,1257.617 238.0672,1257.5371 238.1805,1256.2228 230.7804,1256.3284 228.6235,1254.5622 229.0921,1255.0398 238.2938,1254.9085 238.4071,1253.5942 227.0601,1253.9432 226.435,1250.5339 225.4509,1250.3552 224.1662,1252.5001 224.4263,1253.4155 236.3477,1256.5464 242.5635,1251.4279 242.4936,1252.5232 247.4773,1251.7818 247.3648,1252.4278 256.9612,1248.2083 258.4207,1248.769 257.4675,1249.6932 256.6394,1249.1838 257.805,1248.027 257.5113,1246.9872 255.8113,1248.6744 257.9303,1247.0809 258.4872,1247.3041 258.4613,1246.0645 258.3159,1250.9421 257.0913,1252.5807 257.8913,1252.7999 257.6791,1253.7287 256.609,1253.4355 256.1266,1254.2904 257.4668,1254.6576 257.0423,1256.5153 255.162,1256.0001 254.6796,1256.855 256.83,1257.4442 259.5206,1259.3184 256.4516,1257.9719 256.6177,1258.373 254.1973,1257.7099 254.5168,1257.4558 249.5641,1253.7449 250.8155,1254.9803 249.7819,1255.2883 250.3028,1255.0592 250.1886,1257.0716 248.4233,1260.7751 249.2827,1260.7119 248.5868,1262.1639 246.9772,1273.7178 243.2883,1278.817 242.8564,1280.9769 243.2717,1283.7176 242.3293,1283.5542 241.9901,1286.0615 241.256,1285.9729 240.2036,1287.8943 239.0555,1293.908 236.7374,1292.7849 237.0628,1292.1234 228.494,1288.7939 227.0093,1285.5111 219.3041,1288.15 219.1089,1287.5393 219.3446,1298.656 222.1953,1298.4903 221.9311,1299.3772 221.1547,1299.6398 223.422,1298.5022 223.3835,1299.4582 222.1549,1293.84 220.3345,1294.0242 218.6228,1299.7683 218.2801,1298.4915 217.9298,1299.2563 228.1895,1321.0319 227.1634,1319.1378 228.1446,1317.6522 226.305,1316.3523 240.5056,1311.4094 238.3496,1308.9898 230.4316,1311.8333 231.3065,1312.0682 228.7713,1310.8057 228.8039,1311.8825 225.4466,1313.5669 224.5882,1310.7815 229.4429,1308.3459 229.3646,1307.5219 232.8874,1309.2763 232.7018,1307.8242 236.1937,1306.5702 236.3039,1304.8364 235.4151,1305.2302 234.6738,1301.7416 235.9938,1301.0757 234.0819,1305.9265 234.4684,1306.4843 229.9579,1304.2381 230.0819,1304.8092 223.7298,1307.9961 225.1654,1307.0243 220.571,1297.2731 221.0258,1296.8018 221.4617,1298.795 221.599,1289.8887 221.8809,1290.5812 224.3362,1289.7594 224.1061,1291.1831 228.8215,1292.6882 225.4756,1288.1864 226.3257,1289.8512 235.6754,1293.4679 237.7735,1303.427 238.5905,1303.0881 237.4819,1306.5595 238.2857,1305.4652 250.1904,1322.195 249.6598,1320.8384 227.3234,1325.8037 229.7333,1331.9325 228.8649,1330.9256 238.5578,1328.7709 236.8434,1329.5837 236.4809,1334.8445 236.0858,1334.5448 241.5037,1341.3452 241.0215,1341.0416 236.7604,1351.6985 223.2924,1354.7472 223.055,1353.6728 237.157,1350.6299 236.9537,1352.1521 237.6303,1352.3888 232.4591,1362.657 233.4562,1363.6747 229.503,1365.6922 230.3257,1364.2943 229.3455,1374.9735 230.7711,1375.6381 221.3952,1373.0669 222.3291,1375.4164 224.77,1352.6581 216.0814,1345.5596 216.0245,1346.5968 214.8943,1346.9741 213.1553,1355.6831 212.7361,1354.2464 214.8808,1357.5086 215.4113,1357.3434 206.1549,1366.213 206.5779,1367.1405 217.7781,1356.4083 216.1758,1354.0552 216.752,1355.4832 218.5403,1346.527 221.3772,1350.1325 220.5412,1355.2721 219.6154,1353.864 220.1449,1355.4731 207.0009,1368.0679 207.4239,1368.9953 222.5116,1354.538 223.924,1354.6418 224.214,1353.738 223.9454,1355.0833 224.5142,1355.2774 223.6101,1355.8326 220.1389,1352.9967 225.9299,1349.4836 218.4893,1343.4048 217.9643,1343.7485 218.1936,1344.6556 218.0517,1344.0592 213.8977,1345.4884 210.675,1350.2919 209.5586,1355.8831 209.2965,1354.4377 212.0507,1358.6268 213.0445,1358.2785 205.7319,1365.2856 205.3089,1364.3582 210.6778,1359.2137 209.2205,1359.745 205.8569,1354.6289 206.4558,1353.6098 205.9619,1356.083 202.4172,1354.8201 206.3903,1360.8632 204.4629,1362.5033 204.8859,1363.4308 208.311,1360.1488 203.5602,1361.9815 202.1834,1359.8873"/>
 <polyline points="214.163,1367.8688 209.1159,1372.705 208.6929,1371.7776 216.7698,1364.0382 216.4871,1363.0638 215.3127,1375.8593 214.5525,1376.281 216.8914,1380.0184 215.285

In [103]:
sk.save('/mnt/c/code/side/plotter_images/oned_outputs/236_randomness_y.svg')